In [105]:
! pip install lightgbm --config-settings=cmake.define.USE_OPENMP=OFF

# Прогнозирование заказов такси

Компания «Чётенькое такси» собрала исторические данные о заказах такси в аэропортах. Чтобы привлекать больше водителей в период пиковой нагрузки, нужно спрогнозировать количество заказов такси на следующий час. Необходимо построить модель для прогнозирования стоимости заказа такси, при значении метрики RMSE на тестовой выборке не больее 48.

# Импорты

In [106]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
import seaborn as sns
import matplotlib.pyplot as plt
import plotly.express as px
from statsmodels.stats.outliers_influence import variance_inflation_factor
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import mean_squared_error

from sklearn.linear_model import LinearRegression
from catboost import *
import lightgbm as lgb

from time import time

from sklearn.model_selection import KFold

import optuna
from sklearn.dummy import DummyRegressor


RANDOM_STATE = 1220

# Предобработка данных

In [107]:
df = pd.read_csv('./taxi.csv', index_col=[0], parse_dates=[0])

In [108]:
df.sort_index(inplace=True)


Для анализа временного ряда выполнил ресемплирование в 1 час и посмотрим изменение кривой

In [52]:
df = df.resample('1H').sum()

In [112]:
def make_features(data, max_lag, rolling_mean_size):
    data['year'] = data.index.year
    data['month'] = data.index.month
    data['day'] = data.index.day
    data['dayofweek'] = data.index.dayofweek
    
    for lag in range(1, max_lag + 1):
        data['lag_{}'.format(lag)] = data['num_orders'].shift(lag)

    data['rolling_mean'] = data['num_orders'].shift(1).rolling(rolling_mean_size).mean()

In [113]:
make_features(df, 100, 200)

train, test = train_test_split(df, shuffle=False, test_size=0.1)
train = train.dropna()



/var/folders/n5/30cd9v_56sz_qrnt8mp_9df40000gn/T/ipykernel_1663/705408069.py:8: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data['lag_{}'.format(lag)] = data['num_orders'].shift(lag)
/var/folders/n5/30cd9v_56sz_qrnt8mp_9df40000gn/T/ipykernel_1663/705408069.py:8: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data['lag_{}'.format(lag)] = data['num_orders'].shift(lag)
/var/folders/n5/30cd9v_56sz_qrnt8mp_9df40000gn/T/ipykernel_1663/705408069.py:8: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of c

In [114]:
def info_df(df):
    print('------------------------------')
    print('| Информация о наборе данных |')
    print('------------------------------')
    df.info()
    print('-----------------------------------------')
    print('| Первые и последние 5 строчек датасета |')
    print('-----------------------------------------')
    display(df)
    print('--------------------')
    print('| Сумма дубликатов |')
    print('--------------------')
    print(df.duplicated().sum())
    for i in df.select_dtypes(include='object').columns.to_list():
        print('--------------------------------------')
        print(f'| Уникальные значения признака {i} |')
        print('--------------------------------------')
        print(df[i].unique())

In [115]:
info_df(train)

------------------------------
| Информация о наборе данных |
------------------------------
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 23646 entries, 2018-03-02 09:20:00 to 2018-08-13 14:10:00
Columns: 106 entries, num_orders to rolling_mean
dtypes: float64(101), int64(5)
memory usage: 19.3 MB
-----------------------------------------
| Первые и последние 5 строчек датасета |
-----------------------------------------


num_orders  year  month  day  dayofweek  lag_1  lag_2  \
datetime                                                                     
2018-03-02 09:20:00           9  2018      3    2          4    7.0    6.0   
2018-03-02 09:30:00           7  2018      3    2          4    9.0    7.0   
2018-03-02 09:40:00          11  2018      3    2          4    7.0    9.0   
2018-03-02 09:50:00           5  2018      3    2          4   11.0    7.0   
2018-03-02 10:00:00           6  2018      3    2          4    5.0   11.0   
...                         ...   ...    ...  ...        ...    ...    ...   
2018-08-13 13:30:00          20  2018      8   13          0   34.0   25.0   
2018-08-13 13:40:00          12  2018      8   13          0   20.0   34.0   
2018-08-13 13:50:00           6  2018      8   13          0   12.0   20.0   
2018-08-13 14:00:00          13  2018      8   13          0    6.0   12.0   
2018-08-13 14:10:00           8  2018      8   13          0   13.0    6.0   

                     lag_3  lag_4  lag_5  ...  lag_92  lag_93  lag_94  lag_95  \
datetime                                  ...                                   
2018-03-02 09:20:00   15.0    9.0   12.0  ...    14.0     6.0     9.0     8.0   
2018-03-02 09:30:00    6.0   15.0    9.0  ...    12.0    14.0     6.0     9.0   
2018-03-02 09:40:00    7.0    6.0   15.0  ...    13.0    12.0    14.0     6.0   
2018-03-02 09:50:00    9.0    7.0    6.0  ...    10.0    13.0    12.0    14.0   
2018-03-02 10:00:00    7.0    9.0    7.0  ...     7.0    10.0    13.0    12.0   
...                    ...    ...    ...  ...     ...     ...     ...     ...   
2018-08-13 13:30:00   22.0   16.0   11.0  ...    18.0    21.0    13.0    22.0   
2018-08-13 13:40:00   25.0   22.0   16.0  ...    24.0    18.0    21.0    13.0   
2018-08-13 13:50:00   34.0   25.0   22.0  ...    18.0    24.0    18.0    21.0   
2018-08-13 14:00:00   20.0   34.0   25.0  ...    14.0    18.0    24.0    18.0   
2018-08-13 14:10:00   12.0   20.0   34.0  ...    23.0    14.0    18.0    24.0   

                     lag_96  lag_97  lag_98  lag_99  lag_100  rolling_mean  
datetime                                                                    
2018-03-02 09:20:00     9.0     7.0     5.0     6.0      9.0         9.105  
2018-03-02 09:30:00     8.0     9.0     7.0     5.0      6.0         9.105  
2018-03-02 09:40:00     9.0     8.0     9.0     7.0      5.0         9.070  
2018-03-02 09:50:00     6.0     9.0     8.0     9.0      7.0         8.985  
2018-03-02 10:00:00    14.0     6.0     9.0     8.0      9.0         8.910  
...                     ...     ...     ...     ...      ...           ...  
2018-08-13 13:30:00    20.0    27.0    32.0    21.0     26.0        20.600  
2018-08-13 13:40:00    22.0    20.0    27.0    32.0     21.0        20.635  
2018-08-13 13:50:00    13.0    22.0    20.0    27.0     32.0        20.570  
2018-08-13 14:00:00    21.0    13.0    22.0    20.0     27.0        20.495  
2018-08-13 14:10:00    18.0    21.0    13.0    22.0     20.0        20.425  

[23646 rows x 106 columns]

--------------------
| Сумма дубликатов |
--------------------
0


In [121]:
features_train = train.drop('num_orders', axis=1)
target_train = train['num_orders']

features_test = test.drop('num_orders', axis=1)
target_test = test['num_orders']

In [122]:
vif_data = pd.DataFrame()
vif_data["feature"] = features_train.columns

# вычисление VIF для каждого признака
vif_data["VIF"] = [variance_inflation_factor(features_train.values, i) \
                          for i in range(len(features_train.columns))]

print(vif_data)

KeyboardInterrupt: 

In [60]:
VIF_features_drop = vif_data.query('VIF > 9.0')['feature']
VIF_features_drop

0              year
1             month
104    rolling_mean
Name: feature, dtype: object

In [61]:
features_train_vif = features_train.drop(VIF_features_drop.values, axis=1)
features_test_vif = features_test.drop(VIF_features_drop.values, axis=1)

In [62]:
def metrics(target, prediction, prediction_proba):
    print("F-beta:",fbeta_score(target,prediction,average='macro',beta=2))
    print("AUC-ROC:", roc_auc_score(target, prediction_proba[:, 1]))
    
    fpr, tpr, thresholds = roc_curve(target, prediction_proba[:, 1])
    cm_matrix = pd.DataFrame(data=confusion_matrix(target, prediction), 
                                columns=['Actual Positive:1', 'Actual Negative:0'], 
                                index=['Predict Positive:1', 'Predict Negative:0'])
    tp = cm_matrix['Actual Positive:1']['Predict Positive:1']
    fp = cm_matrix['Actual Positive:1']['Predict Negative:0']
    fn = cm_matrix['Actual Negative:0']['Predict Positive:1']
    tn = cm_matrix['Actual Negative:0']['Predict Negative:0']
    print('Precision =', round(tp / (tp + fp), 3))
    print('Recall = ', round(tp / (tp + fn), 3))

    fig, axes = plt.subplots(ncols=2, figsize=(15, 5))

    sns.heatmap(cm_matrix, annot=True, fmt='d', 
                cmap=sns.diverging_palette(220, 10, as_cmap=True), ax=axes[0])
    axes[1].plot([0, 1], [0, 1], linestyle='--')
    axes[1].plot(fpr, tpr)


    axes[0].title.set_text('Матрица ошибок')
    axes[1].title.set_text('ROC-кривая')
    plt.xlabel('False Positive Rate')
    plt.ylabel('True Positive Rate')
    plt.tight_layout()
    plt.show()

In [63]:
## Linear Regression

In [64]:
model_lr = LinearRegression(n_jobs=10, copy_X=True)

start_time_lr = time()

model_lr.fit(features_train_vif, target_train)

end_time_lr = time()

lr_model_time_fit = (end_time_lr-start_time_lr) / 60

In [65]:
print('Время обучение модели: {0:.5f} сек.'. format(lr_model_time_fit))

Время обучение модели: 0.00060 сек.


In [66]:
start_time_lr = time()
predicted = model_lr.predict(features_train_vif)
end_time_lr = time()

lr_model_time_predict = (end_time_lr-start_time_lr) / 60

In [67]:
model_lr_cv = LinearRegression(n_jobs=10, copy_X=True)

start_time_lr = time()
folds = KFold(n_splits = 4, shuffle = True, random_state = RANDOM_STATE)
scores = cross_val_score(model_lr_cv, features_train_vif, target_train, scoring='neg_root_mean_squared_error', cv=4)
end_time_lr = time()

lr_model_time_cv = (end_time_lr-start_time_lr) / 60

In [96]:
print("RMSE кросс валидации: {0:.2f}.". \
    format(scores.max() * -1))

RMSE кросс валидации: 18.49.


In [97]:
RMSE_LR = scores.max() * -1

## CatBoost

In [69]:
cat_features = features_train_vif.select_dtypes(include='object').columns.to_list()

In [70]:
start_time_cat = time()
cat_model = CatBoostRegressor(loss_function='RMSE',
                                      depth=10,
                                      learning_rate=0.1,
                                      random_state=RANDOM_STATE,
                                      task_type="CPU",
                                      cat_features=cat_features,
                                      ).fit(features_train_vif, target_train,
                                            plot=True, verbose=False)
end_time_cat = time()

cat_model_time_fit = (end_time_cat-start_time_cat) / 60

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

In [71]:
print('Время обучение модели: {0:.5f} сек.'. format(cat_model_time_fit))

Время обучение модели: 0.36860 сек.


In [72]:
start_time_lr = time()
predicted = cat_model.predict(features_train_vif)
end_time_lr = time()

cat_model_time_predict = (end_time_lr-start_time_lr) / 60

In [73]:
print('Время прогнозирования модели: {0:.5f} сек.'. format(cat_model_time_predict))

Время прогнозирования модели: 0.00007 сек.


In [74]:
def objective(trial):
    params = {
        "iterations": 1000,
        "learning_rate": trial.suggest_float("learning_rate", 1e-3, 0.1, log=True),
        "depth": trial.suggest_int("depth", 1, 10),
        "min_data_in_leaf": trial.suggest_int("min_data_in_leaf", 1, 100),
        
    }

    model = CatBoostRegressor(**params, silent=True)
    model.fit(features_train, target_train, cat_features)
    predictions = model.predict(features_train)
    rmse = mean_squared_error(target_train, predictions, squared=True)
    return rmse

In [75]:
study = optuna.create_study(direction="minimize")
study.optimize(objective, n_trials=50)

[I 2024-02-27 16:19:04,591] A new study created in memory with name: no-name-4fcf164d-a219-4278-b23a-e9e37402444d
[I 2024-02-27 16:19:05,070] Trial 0 finished with value: 413.17439382007194 and parameters: {'learning_rate': 0.09980634924820068, 'depth': 1, 'min_data_in_leaf': 50}. Best is trial 0 with value: 413.17439382007194.
[I 2024-02-27 16:19:27,579] Trial 1 finished with value: 274.03754576956277 and parameters: {'learning_rate': 0.005390470982656902, 'depth': 10, 'min_data_in_leaf': 31}. Best is trial 1 with value: 274.03754576956277.
[W 2024-02-27 16:19:27,911] Trial 2 failed with parameters: {'learning_rate': 0.0032037530504706096, 'depth': 6, 'min_data_in_leaf': 43} because of the following error: KeyboardInterrupt('').
Traceback (most recent call last):
  File "/Users/sergeidolin/anaconda3/envs/ds_practicum_env/lib/python3.9/site-packages/optuna/study/_optimize.py", line 200, in _run_trial
    value_or_values = func(trial)
  File "/var/folders/n5/30cd9v_56sz_qrnt8mp_9df40000

KeyboardInterrupt: 

In [ ]:
print('Best hyperparameters:', study.best_params)
print('Best RMSE:', study.best_value**0.5)

Best hyperparameters: {'learning_rate': 0.09691752753013556, 'depth': 10, 'min_data_in_leaf': 41}
Best RMSE: 0.20750604127619893


In [76]:
params_opt = {'learning_rate': 0.09691752753013556, 'depth': 10, 'min_data_in_leaf': 41}

In [77]:
cv_params = cat_model.get_params()
cv_params.update(study.best_params)
cv_data = cv(
    Pool(features_train_vif, target_train, cat_features),
    cv_params,
    plot=True, verbose=False
)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

Training on fold [0/3]

bestTest = 22.02568947
bestIteration = 999

Training on fold [1/3]

bestTest = 23.68664335
bestIteration = 999

Training on fold [2/3]

bestTest = 23.25624209
bestIteration = 999



In [78]:
print('RMSE модели (кросс-валидация): {:.2f}'.format(
    np.min(cv_data['test-RMSE-mean'])
))

RMSE модели (кросс-валидация): 22.99


In [79]:
RMSE_CB = np.min(cv_data['test-RMSE-mean'])

## LithGBM

In [81]:
lgtrain = lgb.Dataset(features_train_vif,target_train ,feature_name = "auto")

In [82]:
hyper_params = {
    'task': 'train',
    'boosting_type': 'gbdt',
    'objective': 'regression',
    'metric': 'rmse',
    'learning_rate': 0.005,
    'feature_fraction': 0.9,
    'bagging_fraction': 0.7,
    'bagging_freq': 10,
    'verbose': 0,
    "max_depth": 8,
    "num_leaves": 128,
    "num_iterations": 1000
}

start_time_lgb = time()
lgb_model = lgb.LGBMRegressor(**hyper_params).fit(features_train_vif, target_train)
end_time_lgb = time()

lgb_model_time_fit = (end_time_lgb-start_time_lgb) / 60

/Users/sergeidolin/anaconda3/envs/ds_practicum_env/lib/python3.9/site-packages/lightgbm/engine.py:172: UserWarning: Found `num_iterations` in params. Will use it instead of argument
  _log_warning(f"Found `{alias}` in params. Will use it instead of argument")


[LightGBM] [Warning] bagging_freq is set=10, subsample_freq=0 will be ignored. Current value: bagging_freq=10
[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] bagging_fraction is set=0.7, subsample=1.0 will be ignored. Current value: bagging_fraction=0.7
[LightGBM] [Warning] bagging_freq is set=10, subsample_freq=0 will be ignored. Current value: bagging_freq=10
[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] bagging_fraction is set=0.7, subsample=1.0 will be ignored. Current value: bagging_fraction=0.7
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -in

In [83]:
print('Время обучение модели: {0:.5f} сек.'. format(lgb_model_time_fit))

Время обучение модели: 0.05841 сек.


In [85]:
start_time_lgb = time()
lgb_pred = lgb_model.predict(features_train_vif, num_iteration=lgb_model.best_iteration_)
end_time_lgb = time()

lgb_model_time_pred = (end_time_lgb-start_time_lgb) / 60

[LightGBM] [Warning] bagging_freq is set=10, subsample_freq=0 will be ignored. Current value: bagging_freq=10
[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] bagging_fraction is set=0.7, subsample=1.0 will be ignored. Current value: bagging_fraction=0.7


In [86]:
print('Время прогнозирования модели: {0:.5f} сек.'. format(lgb_model_time_pred))

Время прогнозирования модели: 0.00378 сек.


In [88]:
def objective_lgb(trial):
    params = {
        'learning_rate': trial.suggest_float("learning_rate", 1e-3, 0.1, log=True),
        'feature_fraction': trial.suggest_float("feature_fraction", 0.1, 0.9, log=True),
        'bagging_fraction': trial.suggest_float("bagging_fraction", 0.1, 0.9, log=True),
        'bagging_freq': trial.suggest_int("bagging_freq", 1, 10),
        'verbose': 0,
        "max_depth": trial.suggest_int("max_depth", 1, 10),
        "num_leaves": trial.suggest_int("num_leaves", 64, 256),
        "num_iterations": 1000
    }

    model = lgb.LGBMRegressor(**params, silent=True)
    model.fit(features_train_vif, target_train)
    predictions = model.predict(features_train_vif)
    rmse = mean_squared_error(target_train, predictions, squared=True)
    return rmse

In [89]:
study = optuna.create_study(direction="minimize")
study.optimize(objective_lgb, n_trials=50)

[I 2024-02-27 16:30:53,187] A new study created in memory with name: no-name-9d4c74ea-3da6-4fe8-849e-be6b3a97e047
/Users/sergeidolin/anaconda3/envs/ds_practicum_env/lib/python3.9/site-packages/lightgbm/engine.py:172: UserWarning: Found `num_iterations` in params. Will use it instead of argument
  _log_warning(f"Found `{alias}` in params. Will use it instead of argument")


[LightGBM] [Warning] Unknown parameter: silent
[LightGBM] [Warning] bagging_freq is set=6, subsample_freq=0 will be ignored. Current value: bagging_freq=6
[LightGBM] [Warning] feature_fraction is set=0.1489671425684063, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.1489671425684063
[LightGBM] [Warning] bagging_fraction is set=0.29358221555802666, subsample=1.0 will be ignored. Current value: bagging_fraction=0.29358221555802666
[LightGBM] [Warning] Unknown parameter: silent
[LightGBM] [Warning] bagging_freq is set=6, subsample_freq=0 will be ignored. Current value: bagging_freq=6
[LightGBM] [Warning] feature_fraction is set=0.1489671425684063, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.1489671425684063
[LightGBM] [Warning] bagging_fraction is set=0.29358221555802666, subsample=1.0 will be ignored. Current value: bagging_fraction=0.29358221555802666
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM

[I 2024-02-27 16:30:53,639] Trial 0 finished with value: 593.0167139851204 and parameters: {'learning_rate': 0.0017375740524235527, 'feature_fraction': 0.1489671425684063, 'bagging_fraction': 0.29358221555802666, 'bagging_freq': 6, 'max_depth': 4, 'num_leaves': 94}. Best is trial 0 with value: 593.0167139851204.
/Users/sergeidolin/anaconda3/envs/ds_practicum_env/lib/python3.9/site-packages/lightgbm/engine.py:172: UserWarning: Found `num_iterations` in params. Will use it instead of argument
  _log_warning(f"Found `{alias}` in params. Will use it instead of argument")


[LightGBM] [Warning] Unknown parameter: silent
[LightGBM] [Warning] bagging_freq is set=6, subsample_freq=0 will be ignored. Current value: bagging_freq=6
[LightGBM] [Warning] feature_fraction is set=0.14212062910790407, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.14212062910790407
[LightGBM] [Warning] bagging_fraction is set=0.10765144974446382, subsample=1.0 will be ignored. Current value: bagging_fraction=0.10765144974446382
[LightGBM] [Warning] Unknown parameter: silent
[LightGBM] [Warning] bagging_freq is set=6, subsample_freq=0 will be ignored. Current value: bagging_freq=6
[LightGBM] [Warning] feature_fraction is set=0.14212062910790407, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.14212062910790407
[LightGBM] [Warning] bagging_fraction is set=0.10765144974446382, subsample=1.0 will be ignored. Current value: bagging_fraction=0.10765144974446382
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[Ligh

[I 2024-02-27 16:30:53,942] Trial 1 finished with value: 350.90791465325077 and parameters: {'learning_rate': 0.016356075091709943, 'feature_fraction': 0.14212062910790407, 'bagging_fraction': 0.10765144974446382, 'bagging_freq': 6, 'max_depth': 4, 'num_leaves': 255}. Best is trial 1 with value: 350.90791465325077.


...

[LightGBM] [Warning] Unknown parameter: silent
[LightGBM] [Warning] bagging_freq is set=9, subsample_freq=0 will be ignored. Current value: bagging_freq=9
[LightGBM] [Warning] feature_fraction is set=0.5594044122253788, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.5594044122253788
[LightGBM] [Warning] bagging_fraction is set=0.6047594160669377, subsample=1.0 will be ignored. Current value: bagging_fraction=0.6047594160669377
[LightGBM] [Warning] Unknown parameter: silent
[LightGBM] [Warning] bagging_freq is set=7, subsample_freq=0 will be ignored. Current value: bagging_freq=7
[LightGBM] [Warning] feature_fraction is set=0.16198211231652215, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.16198211231652215
[LightGBM] [Warning] bagging_fraction is set=0.8987786025999992, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8987786025999992


/Users/sergeidolin/anaconda3/envs/ds_practicum_env/lib/python3.9/site-packages/lightgbm/engine.py:172: UserWarning: Found `num_iterations` in params. Will use it instead of argument
  _log_warning(f"Found `{alias}` in params. Will use it instead of argument")


[LightGBM] [Warning] Unknown parameter: silent
[LightGBM] [Warning] bagging_freq is set=7, subsample_freq=0 will be ignored. Current value: bagging_freq=7
[LightGBM] [Warning] feature_fraction is set=0.16198211231652215, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.16198211231652215
[LightGBM] [Warning] bagging_fraction is set=0.8987786025999992, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8987786025999992
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warni

[I 2024-02-27 16:32:12,810] Trial 49 finished with value: 14.192163793103918 and parameters: {'learning_rate': 0.031470428458796613, 'feature_fraction': 0.16198211231652215, 'bagging_fraction': 0.8987786025999992, 'bagging_freq': 7, 'max_depth': 8, 'num_leaves': 245}. Best is trial 33 with value: 0.04343176575415886.


[LightGBM] [Warning] Unknown parameter: silent
[LightGBM] [Warning] bagging_freq is set=7, subsample_freq=0 will be ignored. Current value: bagging_freq=7
[LightGBM] [Warning] feature_fraction is set=0.16198211231652215, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.16198211231652215
[LightGBM] [Warning] bagging_fraction is set=0.8987786025999992, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8987786025999992


In [90]:
print('Best hyperparameters:', study.best_params)

Best hyperparameters: {'learning_rate': 0.09774515812907832, 'feature_fraction': 0.7556892983168039, 'bagging_fraction': 0.7833320551140095, 'bagging_freq': 8, 'max_depth': 7, 'num_leaves': 212}


In [91]:
params_opt_lgb = {'learning_rate': 0.09774515812907832, 'feature_fraction': 0.7556892983168039, 'bagging_fraction': 0.7833320551140095, 'bagging_freq': 8, 'max_depth': 7, 'num_leaves': 212}

In [92]:
start_time_cb = time()

params_opt_lgb.update({'metric': 'rmse',})
lgbm_cv_model = lgb.cv(params_opt_lgb,
                       train_set=lgtrain,
                       nfold=3)

end_time_cb = time()
    
lgbm_model_time_cv = (end_time_cb-start_time_cb) / 60

/Users/sergeidolin/anaconda3/envs/ds_practicum_env/lib/python3.9/site-packages/sklearn/model_selection/_split.py:684: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=3.
  warnings.warn(


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001162 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 18731
[LightGBM] [Info] Number of data points in the train set: 2516, number of used features: 102
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001182 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 18731
[LightGBM] [Info] Number of data points in the train set: 2516, number of used features: 102
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001185 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 18731
[LightGBM] [Info] Number of data points in the train set: 2516, number of used features: 102
[LightGBM] [Info] Start training from score 79.645072
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[

In [93]:
pd.DataFrame(lgbm_cv_model)

valid rmse-mean  valid rmse-stdv
0         36.443774         0.634140
1         34.512032         0.699364
2         32.880755         0.666584
3         31.425192         0.706029
4         30.123249         0.751103
..              ...              ...
95        22.039299         0.881823
96        22.032298         0.891001
97        22.029712         0.894373
98        22.021935         0.893774
99        22.018818         0.901200

[100 rows x 2 columns]

In [94]:
print('RMSE модели (кросс-валидация): {:.2f}'.format(
    min(pd.DataFrame(lgbm_cv_model)['valid rmse-mean'])
))

RMSE модели (кросс-валидация): 22.02


In [95]:
RMSE_LGBM = min(pd.DataFrame(lgbm_cv_model)['valid rmse-mean'])

In [98]:
results = {
    'Model' : ['LinearRegression', 'CatBoost', 'LightGBM'],
    'Time Fit, sec' : pd.Series([lr_model_time_fit, cat_model_time_fit, lgb_model_time_fit]),
    'Time Pred' :pd.Series([lr_model_time_predict, cat_model_time_predict, lgb_model_time_pred]),
    'RMSE CV' :pd.Series([RMSE_LR, RMSE_CB, RMSE_LGBM])
    }
display(pd.DataFrame(results))

Model  Time Fit, sec  Time Pred    RMSE CV
0  LinearRegression       0.000601   0.000654  18.493066
1          CatBoost       0.368604   0.000071  22.989525
2          LightGBM       0.058413   0.003782  22.016649

In [100]:
dummy_regr = DummyRegressor(strategy="mean")
dummy_regr.fit(features_train_vif, target_train)

DummyRegressor()

In [103]:
lgb_model = lgb.LGBMRegressor(**params_opt_lgb).fit(features_train_vif, target_train)

[LightGBM] [Warning] bagging_freq is set=8, subsample_freq=0 will be ignored. Current value: bagging_freq=8
[LightGBM] [Warning] feature_fraction is set=0.7556892983168039, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.7556892983168039
[LightGBM] [Warning] bagging_fraction is set=0.7833320551140095, subsample=1.0 will be ignored. Current value: bagging_fraction=0.7833320551140095
[LightGBM] [Warning] bagging_freq is set=8, subsample_freq=0 will be ignored. Current value: bagging_freq=8
[LightGBM] [Warning] feature_fraction is set=0.7556892983168039, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.7556892983168039
[LightGBM] [Warning] bagging_fraction is set=0.7833320551140095, subsample=1.0 will be ignored. Current value: bagging_fraction=0.7833320551140095
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001870 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] To

In [104]:
print("RMSE dummy-модели: {0:.2f}.". \
      format((mean_squared_error(target_test, dummy_regr.predict(features_test_vif)))**0.5))
print("Средняя стоимость заказа (DUMMY): {0:.2f}". \
      format(dummy_regr.predict(features_test_vif).mean()))



print("RMSE CatBoost-модели: {0:.2f}.". \
      format((mean_squared_error(target_test, lgb_model.predict(features_test_vif)))**0.5))
print("Средняя стоимость заказа (CatBoost): {0:.2f}". \
      format(cat_model.predict(features_test_vif).mean()))

RMSE dummy-модели: 83.86.
Средняя стоимость заказа (DUMMY): 79.52
[LightGBM] [Warning] bagging_freq is set=8, subsample_freq=0 will be ignored. Current value: bagging_freq=8
[LightGBM] [Warning] feature_fraction is set=0.7556892983168039, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.7556892983168039
[LightGBM] [Warning] bagging_fraction is set=0.7833320551140095, subsample=1.0 will be ignored. Current value: bagging_fraction=0.7833320551140095
RMSE CatBoost-модели: 38.60.
Средняя стоимость заказа (CatBoost): 119.07
